In [1]:
import re
import math
import warnings
import tqdm
import matplotlib
import numpy as np
import pandas as pd
import xgboost as xgb
import matplotlib.pyplot as plt
from scipy.optimize import fsolve
from sympy import symbols, Eq, solve
from matplotlib.pyplot import MultipleLocator
from sklearn.preprocessing import MinMaxScaler, Binarizer
from sklearn.datasets import load_breast_cancer
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import LeaveOneOut
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
warnings.filterwarnings("ignore")


%matplotlib inline
plt.rcParams['font.sans-serif'] = ['SimHei'] 
plt.rcParams['axes.unicode_minus'] = False 

In [2]:
data1=pd.read_excel('/root/GDUT/表1-患者列表及临床信息.xlsx')
data2=pd.read_excel('/root/GDUT/表2-患者影像信息血肿及水肿的体积及位置.xlsx')
data3=pd.read_excel('/root/GDUT/表3-患者影像信息血肿及水肿的形状及灰度分布.xlsx')
data4=pd.read_excel('/root/GDUT/表4-答案文件.xlsx')
data5=pd.read_excel('1b数据.xlsx')

data1.rename(columns={data1.columns[0]: "ID"}, inplace=True)
data2.rename(columns={data2.columns[0]: "ID"}, inplace=True)

data_f_1=pd.read_excel('/root/GDUT/附表1-检索表格-流水号vs时间.xlsx')
data_kz=pd.read_excel('/root/GDUT/q11/扩张及时间.xlsx')

In [3]:
# 转换独热编码
xueya_list = []
for i in data5['血压']:
    y1 = i.split('/')[0]
    y2 = i.split('/')[1]
    if int(y1) > 139 or int(y1) < 90:
        status_i = 0
    elif int(y2) > 89 or int(y2) < 60:
        status_i = 0
    else:
        status_i = 1
    xueya_list.append(status_i)
data5['血压'] = np.array(xueya_list)
data5['性别_男'] = data5['性别'].apply(lambda x: 1 if x == '男' else 0)
data5['性别_女'] = data5['性别'].apply(lambda x: 1 if x == '女' else 0)
data5 = data5.drop(columns=['性别'])
x = data5['年龄'].values
scaler = MinMaxScaler()
x_normalized = scaler.fit_transform(x.reshape(-1, 1))
binarizer = Binarizer(threshold=0.5)
x_binarized = binarizer.fit_transform(x_normalized)
data5['年龄'] = x_binarized
data5 = data5.drop(['流水号'], axis = 1)
data5.head(100)

年龄  脑出血前mRS评分  高血压病史  卒中病史  糖尿病史  房颤史  冠心病史  吸烟史  饮酒史  发病到首次影像检查时间间隔  \
0   0.0          0      0     0     0    0     0    0    0            2.5   
1   0.0          0      1     0     0    0     0    0    0            3.0   
2   1.0          0      1     0     0    0     0    0    0            2.0   
3   1.0          0      1     0     0    0     0    0    0            2.0   
4   1.0          2      1     1     0    0     0    0    0            1.0   
..  ...        ...    ...   ...   ...  ...   ...  ...  ...            ...   
95  0.0          0      1     0     0    0     0    0    0            1.0   
96  1.0          0      0     0     0    0     0    0    0            1.0   
97  1.0          0      1     0     0    0     0    0    0            3.0   
98  1.0          0      1     1     1    1     1    1    0            2.5   
99  0.0          0      1     0     0    0     0    0    0            3.0   

    ...  NCCT_original_firstorder_Median.Hemo  \
0   ...                            180.997857   
1   ...                            137.569328   
2   ...                            133.217856   
3   ...                            133.217856   
4   ...                            124.293778   
..  ...                                   ...   
95  ...                            133.706052   
96  ...                            142.643719   
97  ...                            162.653881   
98  ...                            157.553169   
99  ...                            115.571195   

    NCCT_original_firstorder_Minimum.Hemo  \
0                               86.200064   
1                               69.446385   
2                               61.683739   
3                               61.683739   
4                               59.981668   
..                                    ...   
95                              82.130651   
96                              78.215613   
97                              82.822093   
98                              64.587076   
99                              71.609664   

    NCCT_original_firstorder_Range.Hemo  \
0                            161.239687   
1                            152.848311   
2                            164.933560   
3                            164.933560   
4                            230.164456   
..                                  ...   
95                           133.527068   
96                           146.557579   
97                           169.854351   
98                           157.060233   
99                           193.688206   

    NCCT_original_firstorder_RobustMeanAbsoluteDeviation.Hemo  \
0                                           22.759625           
1                                           26.758880           
2                                           19.037080           
3                                           19.037080           
4                                           21.618937           
..                                                ...           
95                                          18.267232           
96                                          22.871665           
97                                          29.985000           
98                                          16.909283           
99                                          22.412772           

    NCCT_original_firstorder_RootMeanSquared.Hemo  \
0                                      175.551025   
1                                      145.014063   
2                                      135.747065   
3                                      135.747065   
4                                      130.690592   
..                                            ...   
95                                     138.197389   
96                                     145.937323   
97                                     170.381262   
98                                     154.139448   
99                                     132.134408   

    NCCT_origin

In [4]:
# 归一化
# 创建 MinMaxScaler 对象
scaler = MinMaxScaler()
# 选择要归一化的列（除了 '年龄' 列之外的所有列）
columns_to_normalize = [col for col in data5.columns if col != '性别']
# 使用 MinMaxScaler 对所选列进行归一化
data5[columns_to_normalize] = scaler.fit_transform(data5[columns_to_normalize])

In [5]:
data6 = pd.merge(data5.head(100), data_kz['是否扩张'], left_index=True, right_index=True)
data6

年龄  脑出血前mRS评分  高血压病史  卒中病史  糖尿病史  房颤史  冠心病史  吸烟史  饮酒史  发病到首次影像检查时间间隔  \
0   0.0   0.000000    0.0   0.0   0.0  0.0   0.0  0.0  0.0       0.094737   
1   0.0   0.000000    1.0   0.0   0.0  0.0   0.0  0.0  0.0       0.115789   
2   1.0   0.000000    1.0   0.0   0.0  0.0   0.0  0.0  0.0       0.073684   
3   1.0   0.000000    1.0   0.0   0.0  0.0   0.0  0.0  0.0       0.073684   
4   1.0   0.666667    1.0   1.0   0.0  0.0   0.0  0.0  0.0       0.031579   
..  ...        ...    ...   ...   ...  ...   ...  ...  ...            ...   
95  0.0   0.000000    1.0   0.0   0.0  0.0   0.0  0.0  0.0       0.031579   
96  1.0   0.000000    0.0   0.0   0.0  0.0   0.0  0.0  0.0       0.031579   
97  1.0   0.000000    1.0   0.0   0.0  0.0   0.0  0.0  0.0       0.115789   
98  1.0   0.000000    1.0   1.0   1.0  1.0   1.0  1.0  0.0       0.094737   
99  0.0   0.000000    1.0   0.0   0.0  0.0   0.0  0.0  0.0       0.115789   

    ...  NCCT_original_firstorder_Minimum.Hemo  \
0   ...                               0.580976   
1   ...                               0.302489   
2   ...                               0.173455   
3   ...                               0.173455   
4   ...                               0.145162   
..  ...                                    ...   
95  ...                               0.513332   
96  ...                               0.448255   
97  ...                               0.524826   
98  ...                               0.221715   
99  ...                               0.338448   

    NCCT_original_firstorder_Range.Hemo  \
0                              0.461355   
1                              0.415018   
2                              0.481753   
3                              0.481753   
4                              0.841963   
..                                  ...   
95                             0.308324   
96                             0.380280   
97                             0.508926   
98                             0.438276   
99                             0.640538   

    NCCT_original_firstorder_RobustMeanAbsoluteDeviation.Hemo  \
0                                            0.596541           
1                                            0.784219           
2                                            0.421848           
3                                            0.421848           
4                                            0.543010           
..                                                ...           
95                                           0.385720           
96                                           0.601798           
97                                           0.935615           
98                                           0.321994           
99                                           0.580263           

    NCCT_original_firstorder_RootMeanSquared.Hemo  \
0                                        0.747897   
1                                        0.401521   
2                                        0.296407   
3                                        0.296407   
4                                        0.239052   
..                                            ...   
95                                       0.324200   
96                                       0.411993   
97                                       0.689257   
98                                       0.505029   
99                                       0.255429   

    NCCT_original_firstorder_Skewness.Hemo  \
0                                 0.073091   
1                                 0.432276   
2                                 0.379049   
3                                 0.379049   
4                                 0.550780   
..                                     ...   
95                                0.498901   
96                                0.372799   
97                                0.403759   
98                                0.035582   
99                                0.76

In [6]:
X = data6.drop(columns=['是否扩张'])  # 特征列
y = data6['是否扩张']  # 目标列

In [7]:
# 将数据划分为80%的训练集和20%的测试集
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# X_train包含训练集的特征
# y_train包含训练集的目标标签
# X_test包含测试集的特征
# y_test包含测试集的目标标签

In [8]:
# 定义超参数的候选值
param_grid = {
    'n_estimators': [50, 100, 150, 200],
    'max_depth': [None, 10, 20, 30],
    'min_samples_split': [2, 4, 6, 8, 10],
    'min_samples_leaf': [1, 2, 4]
}

# 创建随机森林分类器
rf_classifier = RandomForestClassifier(random_state=0)

In [ ]:
# 随机森林 + 网格搜索 - 5折交叉验证 - 4进程
grid_search = GridSearchCV(rf_classifier, param_grid, cv=5, scoring='accuracy', n_jobs=3)
grid_search.fit(X_train, y_train)
best_params = grid_search.best_params_
print(f"训练集最佳超参数组合: {best_params}")
best_model_rf1 = grid_search.best_estimator_
y_pred = best_model_rf1.predict(X)
accuracy = accuracy_score(y_train, y_pred)
print(f"训练集最佳模型的准确率: {accuracy:.4f}")
best_model_rf1 = grid_search.best_estimator_
y_pred = best_model_rf1.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"测试集最佳模型的准确率: {accuracy:.4f}")

In [ ]:
# 随机森林 + 留一交叉验证 + 网格搜索 - 5折交叉验证 - 4进程
loo = LeaveOneOut()
grid_search = GridSearchCV(rf_classifier, param_grid, cv=loo, scoring='accuracy', n_jobs=3)
grid_search.fit(X_train, y_train)
best_params = grid_search.best_params_
print(f"训练集最佳超参数组合: {best_params}")
best_model_rf2 = grid_search.best_estimator_
y_pred = best_model_rf2.predict(X)
accuracy = accuracy_score(y_train, y_pred)
print(f"训练集最佳模型的准确率: {accuracy:.4f}")
best_model_rf2 = grid_search.best_estimator_
y_pred = best_model_rf2.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"测试集最佳模型的准确率: {accuracy:.4f}")

In [ ]:
# # XGBoost + 留一交叉验证 + 网格搜索 + 4进程
# warnings.filterwarnings("ignore", category=FutureWarning)
# xgb_classifier = xgb.XGBClassifier(random_state=0)

# param_grid = {
#     'n_estimators': [50, 100, 200],
#     'max_depth': [3, 4, 5],
#     'learning_rate': [0.01, 0.1, 0.2],
#     'min_child_weight': [1, 2, 3]
# }


# loo = LeaveOneOut()

# grid_search = GridSearchCV(xgb_classifier, param_grid, cv=loo, scoring='accuracy', n_jobs=4)
# grid_search.fit(X, y)

# best_params = grid_search.best_params_
# print(f"最佳超参数组合: {best_params}")

# best_model_xgb = grid_search.best_estimator_
# y_pred = best_model_xgb.predict(X)
# accuracy = accuracy_score(y, y_pred)
# print(f"最佳模型的准确率: {accuracy:.4f}")

/root/miniconda3/envs/jupyter-env/lib/python3.11/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/root/miniconda3/envs/jupyter-env/lib/python3.11/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/root/miniconda3/envs/jupyter-env/lib/python3.11/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/root/miniconda3/envs/jupyter-env/lib/python3.11/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
 

In [ ]:
# 测试集预测
# probabilities = best_model.predict_proba(data5.tail(len(data5) - 100))